# Twitter Activity Analysis Notework for Dark 26 

In [1]:
#Import libraries
import pandas as pd
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import json
import seaborn as sns
import math
import re
import nltk
# nltk.download('punkt')
# nltk.download('stopwords')
from nltk.probability import FreqDist
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import pytz
from pytz import timezone
import datetime
import time
import collections
from wordcloud import WordCloud
import settings
import mysql.connector
import itertools
import os 
import psycopg2
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import plotly
import random
import plotly.express as px
from IPython.display import clear_output
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots
py.init_notebook_mode()

In [2]:
# Dictionary of US State names used for in constructing map
STATES = ['Alabama', 'AL', 'Alaska', 'AK', 'American Samoa', 'AS', 'Arizona', 'AZ', 'Arkansas', 'AR', 'California', 'CA', 'Colorado', 'CO', 'Connecticut', 'CT', 'Delaware', 'DE', 'District of Columbia', 'DC', 'Federated States of Micronesia', 'FM', 'Florida', 'FL', 'Georgia', 'GA', 'Guam', 'GU', 'Hawaii', 'HI', 'Idaho', 'ID', 'Illinois', 'IL', 'Indiana', 'IN', 'Iowa', 'IA', 'Kansas', 'KS', 'Kentucky', 'KY', 'Louisiana', 'LA', 'Maine', 'ME', 'Marshall Islands', 'MH', 'Maryland', 'MD', 'Massachusetts', 'MA', 'Michigan', 'MI', 'Minnesota', 'MN', 'Mississippi', 'MS', 'Missouri', 'MO', 'Montana', 'MT', 'Nebraska', 'NE', 'Nevada', 'NV', 'New Hampshire', 'NH', 'New Jersey', 'NJ', 'New Mexico', 'NM', 'New York', 'NY', 'North Carolina', 'NC', 'North Dakota', 'ND', 'Northern Mariana Islands', 'MP', 'Ohio', 'OH', 'Oklahoma', 'OK', 'Oregon', 'OR', 'Palau', 'PW', 'Pennsylvania', 'PA', 'Puerto Rico', 'PR', 'Rhode Island', 'RI', 'South Carolina', 'SC', 'South Dakota', 'SD', 'Tennessee', 'TN', 'Texas', 'TX', 'Utah', 'UT', 'Vermont', 'VT', 'Virgin Islands', 'VI', 'Virginia', 'VA', 'Washington', 'WA', 'West Virginia', 'WV', 'Wisconsin', 'WI', 'Wyoming', 'WY']
STATE_DICT = dict(itertools.zip_longest(*[iter(STATES)] * 2, fillvalue=""))
INV_STATE_DICT = dict((v,k) for k,v in STATE_DICT.items())
pd.options.display.max_colwidth = 200

In [3]:
# Load data from local Postgresql database
# DATABASE_URL = os.environ['DATABASE_URL'] 
# conn = connect(DATABASE_URL)
# conn = psycopg2.connect(DATABASE_URL, sslmode='require')
TABLE_NAME = "dark26_"
conn = psycopg2.connect(user = "root",
                        password = "",
                        host = "localhost",
                        port = "5432",
                        database = "dbtwitter")

In [4]:
# Uncomment to specific time_start and timedelta in UTC
time_start = datetime.datetime(2020, 3, 24, hour=22, minute=0, second=0, microsecond=0, tzinfo=pytz.utc)
timedelta = datetime.timedelta(hours=3, minutes=0, seconds=59)
time_end = time_start + timedelta

time_start_str = time_start.strftime('%Y-%m-%d %H:%M:%S')
time_end_str = time_end.strftime('%Y-%m-%d %H:%M:%S')

time_start_CST = time_start.astimezone(timezone('US/Central')).strftime('%b %d, %Y %I:%M%p')
time_end_CST = time_end.astimezone(timezone('US/Central')).strftime('%b %d, %Y %I:%M%p')
query = "SELECT * FROM {} WHERE created_at >= '{}' AND created_at <= '{}'".format(TABLE_NAME, time_start_str, time_end_str)

In [5]:
# Selects all tweets from specified table
# query = "SELECT * FROM {} ".format(TABLE_NAME)

# Run query to get data and read into Pandas DataFrame
tweets_df = pd.read_sql(query, con=conn)

In [6]:
#tweets_df.head()

In [7]:
# Clean columns and replace None with blank
tweets_df['in_reply_to'] = tweets_df['in_reply_to'].apply(lambda i : i or '')
# tweets_df['text'] = tweets_df['text'].apply(lambda text: text.encode('ascii', 'ignore').decode('ascii'))
tweets_df['was_retweet_user'] = tweets_df['was_retweet_user'].apply(lambda i : i or '')
tweets_df['was_retweet_id'] = tweets_df['was_retweet_id'].apply(lambda i : i or '')
# Add column is_retweet 
tweets_df['is_retweet'] = tweets_df['text'].apply(lambda x: False if 'RT' not in x else True)
# Convert created_at and user_created time to CST
tweets_df['created_at'] = pd.to_datetime(tweets_df['created_at'], format = '%Y-%m-%d %H:%M:%S', utc=True)
# tweets_df['created_at'] = tweets_df['created_at'].dt.tz_localize('utc')
tweets_df['created_at'] = tweets_df['created_at'].dt.tz_convert('US/Central')
tweets_df['user_created'] = pd.to_datetime(tweets_df['user_created'], format = '%Y-%m-%d %H:%M:%S', utc=True)
# tweets_df['user_created'] = tweets_df['user_created'].dt.tz_localize('utc')
tweets_df['user_created'] = tweets_df['user_created'].dt.tz_convert('US/Central')
tweets_df['text_lower'] = tweets_df['text'].apply(lambda x:x.lower())

In [8]:
# Compute # of RT's, @'s, and text tweets
retweet_tweets = tweets_df[tweets_df['is_retweet'] == True]
response_tweets = tweets_df[tweets_df['in_reply_to']!='']
mention_tweets = tweets_df[~tweets_df['text'].str.contains("RT")  & tweets_df['text'].str.contains("@")]
mention_tweets = mention_tweets[mention_tweets['in_reply_to']==""]
text_tweets = tweets_df[~tweets_df['text'].str.contains("@")  & ~tweets_df['text'].str.contains("RT")]
url_tweets = tweets_df[tweets_df['text'].str.contains("http")]

In [9]:
# Determine timestamp of first and last tweet in the data
time_start = tweets_df['created_at'].min()
time_end = tweets_df['created_at'].max()
# Determine time duration
timedelta = time_end - time_start
time_start_CST = tweets_df['created_at'].min().strftime('%b %d, %Y %I:%M%p')
time_end_CST = tweets_df['created_at'].max().strftime('%b %d, %Y %I:%M%p')

In [10]:
print("Tweets were collected from {} to {}".format(time_start_CST,time_end_CST))
print("Time duration: {}".format(timedelta))

Tweets were collected from Mar 24, 2020 05:00PM to Mar 24, 2020 08:00PM
Time duration: 0 days 03:00:51


In [11]:
print("Total number of tweets: {}".format(len(tweets_df)))
print("Number of unique users: {}".format(tweets_df['user_name'].nunique()))
print("Average number of Tweets Per User: {0:.2f}".format(len(tweets_df)/tweets_df['user_name'].nunique()))                                   
print("Average Number of Tweets Per Minute: {0:.2f}".format(len(tweets_df)/int(timedelta.total_seconds() / 60)))
print("------")
print("Total number of retweets:", len(retweet_tweets))
print("Total number of response tweets:", len(response_tweets))
print("Total number of tweets with mentions that are not retweets or responses:", len(mention_tweets))
print("Total number of text tweets:", len(text_tweets))
print("Number of tweets containing URL links:", len(url_tweets))

Total number of tweets: 3690
Number of unique users: 1525
Average number of Tweets Per User: 2.42
Average Number of Tweets Per Minute: 20.50
------
Total number of retweets: 2384
Total number of response tweets: 167
Total number of tweets with mentions that are not retweets or responses: 332
Total number of text tweets: 824
Number of tweets containing URL links: 1569


In [12]:
# Pie chart of percentage of tweets by type
values = [ len(retweet_tweets), len(response_tweets), len(mention_tweets), len(text_tweets)]
labels = ['Retweets', 'Responses', 'Mentions', 'Text tweets']
fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.update_layout(
    title_text = 'Percentage of Tweets by Type'
)
# fig.write_image("images/percentage_of_tweets_by_type.png")
fig.show()

In [13]:
tweet_dist = pd.DataFrame(list(zip(labels, values)), columns =['Type', 'Freq'])
tweet_dist.to_csv("output/percentage of tweets by type.csv", index=False)

In [14]:
# Build geographic map showing user locations
is_in_US=[]
geo = tweets_df[['user_location']]
tweets_df = tweets_df.fillna(" ")
for x in tweets_df['user_location']:
    check = False
    for s in STATES:
        if s in x:
            is_in_US.append(STATE_DICT[s] if s in STATE_DICT else s)
            check = True
            break
    if not check:
        is_in_US.append(None)
is_in_US
geo_dist = pd.DataFrame(is_in_US, columns=['State']).dropna().reset_index()
geo_dist = geo_dist.groupby('State').count().rename(columns={"index": "Number"}) \
        .sort_values(by=['Number'], ascending=False).reset_index()
geo_dist["Log Num"] = geo_dist["Number"].apply(lambda x: math.log(x, 2))
geo_dist['Full State Name'] = geo_dist['State'].apply(lambda x: INV_STATE_DICT[x])
geo_dist['text'] = geo_dist['Full State Name'] + '<br>' + 'Num: ' + geo_dist['Number'].astype(str)

fig = go.Figure(data=go.Choropleth(
    locations=geo_dist['State'], # Spatial coordinates
    z = geo_dist['Number'].astype(float), # Data to be color-coded
    locationmode = 'USA-states', # set of locations match entries in `locations`
    colorscale = 'Blues',
    colorbar_title = "Number of tweets",
))
fig.update_layout(
    title_text = 'Tweets by User Location',
    geo_scope='usa', # limite map scope to USA
)
# fig.write_image("images/tweets_by_user_location.png")
fig.show()

In [15]:
map_freq = geo_dist[['State','Number','Log Num','Full State Name','text']]
map_freq.to_csv("output/tweets by user location.csv", index=False)

In [16]:
# Time series of number of tweets over time
total = tweets_df.groupby(pd.Grouper(key='created_at', freq='1min')).count().reset_index()
total = total.rename(columns={"user_name": "Num of tweets", "created_at":"Time in CST"})  
time_series = total["Time in CST"].reset_index(drop=True)
# result = tweets_df.groupby([pd.Grouper(key='created_at', freq='1min'), 'sentiment']).count().unstack(fill_value=0).stack().reset_index()
# result = result.rename(columns={"user_name": "Num of tweets", "created_at":"Time in CST"})  
# time_series_ = result["Time in CST"][result['sentiment']==0].reset_index(drop=True)
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=time_series,
    y=total["Num of tweets"],
    name="Total",
    opacity=0.8))

fig.update_layout(
    title="Number of Tweets over time",
    xaxis_title="Time in CST",
    yaxis_title="Frequency",
)

fig.add_shape(
    dict(
      type= 'line',
      yref= 'paper', y0= 0, y1= 1,
      xref= 'x', x0= '2020-03-24 18:00:00-05:00', x1= '2020-03-24 18:00:00-05:00',
    line=dict(
    color="black",
    width=1,
    dash="dot",
    )
))
fig.add_shape(
    dict(
      type= 'line',
      yref= 'paper', y0= 0, y1= 1,
      xref= 'x', x0= '2020-03-24 19:00:00-05:00', x1= '2020-03-24 19:00:00-05:00',
    line=dict(
    color="black",
    width=1,
    dash="dot",
    )
))
# fig.write_image("images/number_of_tweets_over_time.png")
fig.show()

In [17]:
time_freq = total[['Time in CST','Num of tweets']]
time_freq.to_csv("output/tweets over time.csv", index=False)

In [18]:
not_retweets_df = tweets_df[tweets_df['is_retweet'] == False]
retweets_df = tweets_df[tweets_df['is_retweet'] == True]

print("Total number of tweets that are not retweets: {}".format(len(not_retweets_df)))
print("Total number of tweets that are retweets: {}".format(len(retweets_df)))

# Time series of number of tweets over time
total = tweets_df.groupby(pd.Grouper(key='created_at', freq='1min')).count().reset_index()
total = total.rename(columns={"user_name": "Num of tweets", "created_at":"Time in CST"})  
time_series = total["Time in CST"].reset_index(drop=True)
subset_one = retweets_df.groupby(pd.Grouper(key='created_at', freq='1min')).count().reset_index()
subset_one = subset_one.rename(columns={"user_name": "Num of tweets", "created_at":"Time in CST"})  
time_series = subset_one["Time in CST"].reset_index(drop=True)

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=time_series,
    y=total["Num of tweets"],
    name="Total",
    opacity=0.8,
    fill='tozeroy')
)
fig.add_trace(go.Scatter(
    x=time_series,
    y=subset_one["Num of tweets"],
    name="Retweets",
    opacity=0.8,
    fill='tozeroy'), 
)

fig.update_layout(
    title="Number of Tweets over time",
    xaxis_title="Time in CST",
    yaxis_title="Frequency",
)

fig.add_shape(
    dict(
      type= 'line',
      yref= 'paper', y0= 0, y1= 1,
      xref= 'x', x0= '2020-03-24 18:00:00-05:00', x1= '2020-03-24 18:00:00-05:00',
    line=dict(
    color="black",
    width=1,
    dash="dot",
    )
))
fig.add_shape(
    dict(
      type= 'line',
      yref= 'paper', y0= 0, y1= 1,
      xref= 'x', x0= '2020-03-24 19:00:00-05:00', x1= '2020-03-24 19:00:00-05:00',
    line=dict(
    color="black",
    width=1,
    dash="dot",
    )
))
# fig.write_image("images/number_of_tweets_over_time_sentiment.png")
fig.show()

Total number of tweets that are not retweets: 1306
Total number of tweets that are retweets: 2384


In [19]:
# Find most used hashtags
hashtags = []
hashtag_pattern = re.compile(r"#[a-zA-Z0-9]+")
hashtag_matches = list(tweets_df['text'].apply(hashtag_pattern.findall))
hashtag_words = []
for match in hashtag_matches:
    for word in match:
        hashtag_words.append(word.lower())
fdist = FreqDist(hashtag_words)
fd = pd.DataFrame(fdist.most_common(50), columns = ["Hashtags","Frequency"]).reindex()

In [20]:
fd.to_csv("output/top 50 hashstag frequency.csv", index=False)
# Generate HTML for table
# print("<table class=\"table table-striped table-bordered\">")
# print("<thead>\n<tr>\n<th scope=\"col\">Hashtags</th>")
# print("<th scope=\"col\">Frequency</th>\n</tr>\n</thead>")
# print("<tbody>")
# top = fd.head(20)
# for index, row in top.iterrows():
#     line = "<tr><td>" + row['Hashtags'] + "</td><td>" + str(row['Frequency']) + "</td></tr>"
#     print(line)
# print("</tbody>")
# print("</table>")

In [21]:
fig = go.Figure(
    data=go.Table(header=dict(
        values=['Hashtags', 'Frequency']),
        cells=dict(values=[fd["Hashtags"], fd["Frequency"]])
    ))
    
fig.update_layout(
    title_text = 'Top 50 Most Frequent Hashtags',
)
# fig.write_image("images/most_frequent_hashtags_table.png", width=900, height=650)
fig.show()

In [22]:
# Number of mentions for a particular hashtag
hashtag = "#aewdark"
mentioned_values = pd.concat([tweets_df['created_at'], tweets_df['text_lower'].apply(hashtag_pattern.findall)], axis=1, keys=['created_at', 'values'])
mentioned_values = mentioned_values.explode('values')
mentioned = mentioned_values.groupby('values')
item = mentioned.get_group(hashtag) 
total = item.groupby(pd.Grouper(key='created_at', freq='1min')).count().reset_index()
total = total.rename(columns={"values": "Num of Mentions", "created_at":"Time in CST"})  
time_series = total["Time in CST"].reset_index(drop=True)

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=time_series,
    y=total["Num of Mentions"],
    name="Total",
    opacity=0.8,
    )
)

fig.update_layout(
    title="Number of Mentions over time",
    xaxis_title="Time in CST",
    yaxis_title="Frequency",
    xaxis  = go.layout.XAxis( range = ['2020-03-24 17:00:00-05:00', '2020-03-24 20:00:00-05:00']),

)
fig.show()



In [23]:
def grey_color_func(word, font_size, position,orientation,random_state=None, **kwargs):
    return("hsl(241, 85%, 46%)")

#Make a wordcloud plot of the most used hashtags
tuples = [tuple(x) for x in fd.values]
wordcloud = WordCloud(width=1000, height=600, random_state=21, max_font_size=200, background_color = 'white').generate_from_frequencies(dict(tuples))
wordcloud.recolor(color_func = grey_color_func)
plt.figure(figsize=(15, 10))
plt.imshow(wordcloud, interpolation="bilinear")
plt.axis('off')
# plt.savefig('images/most_frequent_hashtags_cloud.png')
plt.show()

In [38]:
# Find most mentioned accounts 
# mentions_df = tweets_df[tweets_df['was_retweet_id']==''] #tweets that are not retweets
# mentions_df = mentions_df[mentions_df['in_reply_to']==''] #tweets that are not responses
mentions = []
mention_pattern = re.compile(r"@[a-zA-Z_0-9]+")
mention_matches = list(tweets_df['text'].apply(mention_pattern.findall))
mentioned_accounts = []
for match in mention_matches:
    for word in match:
        mentioned_accounts.append(word.lower())
fdist = FreqDist(mentioned_accounts)
fd = pd.DataFrame(fdist.most_common(50), columns = ["Value","Frequency"])
fd['Link'] = fd['Value'].apply(lambda x: "<a href=\"http://www.twitter.com/" 
                                 + re.sub(r"\@", "", str(x)) + "\">" + str(x) + "</a>")
fig = go.Figure(
    data=go.Table(header=dict(
        values=['Username', 'Frequency']),
        cells=dict(values=[fd["Link"], fd["Frequency"]])
    ))
    
fig.update_layout(
    title_text = 'Top 50 Most Mentioned Accounts',
)
fig.show()

In [56]:
# Bar chart with number of mentions for set of usernames
usernames = ['@RealJakeHager','@JoeAlonzoJr','@dustinrhodes','@realmmarshall1',\
             '@kingserpentico','@AllSellsFinal', '@facdaniels', '@frankiekazarian',
             '@Egos1313', '@Perfec10n'\
             '@thekipsabian', '@SugarDunkerton','@coltcabana','@brancutler',\
             '@janelababy','@sonnykissxo','@CoreyHollis','@upgrademikereed']
usernames = [x.lower() for x in usernames]          
fdist = FreqDist(mentioned_accounts)
fd = pd.DataFrame(fdist.most_common(50), columns = ["Value","Frequency"])
fd = fd[fd['Value'].isin(usernames)]
trace = go.Bar(x=fd["Value"], y=fd["Frequency"], name="Freq Dist")
fig = go.Figure(trace)
fig.update_layout(
    title="Number of Mentions",
    xaxis_title="Username",
    yaxis_title="Frequency",
)
fig.show()

In [25]:
# Number of mentions for a particular username over time
user_name = "@sugardunkerton"
user_name2 = "@thekipsabian"
mentioned_values = pd.concat([tweets_df['created_at'], tweets_df['text_lower'].apply(mention_pattern.findall)], axis=1, keys=['created_at', 'values'])
mentioned_values = mentioned_values.explode('values')
mentioned = mentioned_values.groupby('values')

item = mentioned.get_group(user_name.lower()) 
total = item.groupby(pd.Grouper(key='created_at', freq='1min')).count().reset_index()
total = total.rename(columns={"values": "Num of Mentions", "created_at":"Time in CST"})  
time_series = total["Time in CST"].reset_index(drop=True)

item2 = mentioned.get_group(user_name2.lower()) 
total_two = item2.groupby(pd.Grouper(key='created_at', freq='1min')).count().reset_index()
total_two = total_two.rename(columns={"values": "Num of Mentions", "created_at":"Time in CST"})  
time_series_two = total_two["Time in CST"].reset_index(drop=True)

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=time_series,
    y=total["Num of Mentions"],
    name=user_name,
    opacity=0.8)
)
fig.add_trace(go.Scatter(
    x=time_series_two,
    y=total_two["Num of Mentions"],
    name=user_name2,
    opacity=0.8)
)

fig.update_layout(
    title="Number of Mentions over time",
    xaxis_title="Time in CST",
    yaxis_title="Frequency",
    xaxis  = go.layout.XAxis( range = ['2020-03-24 17:00:00-05:00', '2020-03-24 20:00:00-05:00']),
)
fig.show()

In [26]:
#Make a wordcloud representation
tuples = [tuple(x) for x in fd[['Value','Frequency']].values]
wordcloud = WordCloud(width=1000, height=600, random_state=21, max_font_size=200, background_color = 'white').generate_from_frequencies(dict(tuples))
plt.figure(figsize=(15, 10))
plt.imshow(wordcloud, interpolation="bilinear")
plt.axis('off')
plt.show()

In [27]:
# Most retweeted tweets
retweeted_tweets = tweets_df[tweets_df['was_retweet_id']!='']
retweeted_tweets = retweeted_tweets['was_retweet_id']
fdist = FreqDist(retweeted_tweets)
fd = pd.DataFrame(fdist.most_common(20), columns = ["Tweet id","Frequency"])
retweeted_tweets_links = []
# fd['url'] = fd['Tweet id'].apply(lambda x: "http://www.twitter.com/user/status/" + str(x))
fd['Link'] = fd['Tweet id'].apply(lambda x: "<a href=\"http://www.twitter.com/user/status/" + str(x) + "\">" + str(x) + "</a>")

In [28]:
fd.to_csv("output/top 20 retweeted frequency.csv", index=False)
# Generate HTML for table
# print("<table class=\"table table-striped table-bordered\">")
# print("<thead>\n<tr>\n<th scope=\"col\">Tweet ID</th>")
# print("<th scope=\"col\">Frequency</th>\n</tr>\n</thead>")
# print("<tbody>")
# top = fd.head(10)
# for index, row in top.iterrows():
#     line = "<tr><td>@" + row['Link'] + "</td><td>" + str(row['Frequency']) + "</td></tr>"
#     print(line)
# print("</tbody>")
# print("</table")

In [29]:
fig = go.Figure(
    data=go.Table(header=dict(
        values=['Tweet ID', 'Frequency']),
        cells=dict(values=[fd["Link"], fd["Frequency"]])
    ))
    
fig.update_layout(
    title_text = 'Top 20 Most Retweeted Tweets',
)
# fig.write_image("images/most_retweeted_tweets.png", width=900, height=650)
fig.show()

In [30]:
# Most retweeted accounts
retweeted_accounts = tweets_df[tweets_df['was_retweet_user']!='']
retweeted_accounts = retweeted_accounts['was_retweet_user']
retweeted_accounts
fdist = FreqDist(retweeted_accounts)
fd = pd.DataFrame(fdist.most_common(50), columns = ["Username","Frequency"])

fig = go.Figure(
    data=go.Table(header=dict(
        values=['Username', 'Frequency']),
        cells=dict(values=[fd["Username"], fd["Frequency"]])
    ))
    
fig.update_layout(
    title_text = 'Top 50 Most Retweeted Accounts',
)
# fig.write_image("images/most_retweeted_accounts_table.png",width=900, height=650)
fig.show()

In [31]:
fd.to_csv("output/top 50 retweeted users frequency.csv", index=False)
# Generate HTML for table
# print("<table class=\"table table-striped table-bordered\">")
# print("<thead>\n<tr>\n<th scope=\"col\">Username</th>")
# print("<th scope=\"col\">Frequency</th>\n</tr>\n</thead>")
# print("<tbody>")
# top = fd.head(10)
# for index, row in top.iterrows():
#     line = "<tr><td>@" + row['Username'] + "</td><td>" + str(row['Frequency']) + "</td></tr>"
#     print(line)
# print("</tbody>")
# print("</table")